## Data Cleaning 

Include physiochemcial properties

In [41]:
#import libraries
import pandas as pd
import numpy as np
pd.set_option('display.max_columns', None )

## Yield Data

In [42]:
#import yield data
yld = pd.read_csv('../data/SAP2020_merged_v2.csv')
yld.head(3)

PlotIDYellow  PlotIDRed SorghumAccessionYellow SorghumAccessionRed  \
0          9844     8390.0              PI 655998           PI 655998   
1          8390     8377.0              PI 564163              BTx623   
2          8377     8364.0              PI 576396           PI 576396   

  SorghumNameRed  SNPDataID  Row  Column  Block           Treatment  \
0           KS19      294.0   69     1.0      8  SufficientNitrogen   
1         BTx623      160.0   69     2.0      8  SufficientNitrogen   
2         SC_324      196.0   69     3.0      8  SufficientNitrogen   

   DaysToBloom  MedianLeafAngle  LeafAngleSDV PoorStand?  PaniclesPerPlot  \
0         62.0             43.2          6.29          N             15.0   
1         65.0             43.7          7.11          Y             11.0   
2         64.0             45.4          7.80          N             12.0   

   PanicleGrainWeight  EstimatedPlotYield  FlagLeafLength  FlagLeafWidth  \
0                20.0               300.0            50.1            4.5   
1                 NaN                 NaN            34.0            5.3   
2                38.0               456.0            24.2            3.6   

   ExtantLeafNumber  PlantHeight  ThirdLeafLength  ThirdLeafWidth  \
0              11.0         86.0             68.0             6.0   
1              12.0        102.0             72.0             8.0   
2              12.0         90.0             60.0             5.0   

   TillersPerPlant  StemDiameterLower  StemDiameterUpper  RachisLength  \
0             0.00              21.01               9.92         27.37   
1             0.67              25.89              11.19         27.10   
2             0.00              16.02               7.30          9.63   

   RachisDiameterLower  RachisDiameterUpper  PrimaryBranchNo  \
0                 6.31                 1.78            81.00   
1                 6.96                 2.66            60.00   
2                 5.42                 4.61            35.33   

   BranchInternodeLength  
0                   1.80  
1                   1.87  
2                   1.77

In [43]:
yld.isnull().sum()

PlotIDYellow                0
PlotIDRed                   6
SorghumAccessionYellow      3
SorghumAccessionRed         6
SorghumNameRed              6
SNPDataID                   8
Row                         0
Column                      1
Block                       0
Treatment                   0
DaysToBloom                86
MedianLeafAngle            80
LeafAngleSDV              143
PoorStand?                  1
PaniclesPerPlot           507
PanicleGrainWeight        327
EstimatedPlotYield        685
FlagLeafLength            505
FlagLeafWidth             504
ExtantLeafNumber          458
PlantHeight               459
ThirdLeafLength           592
ThirdLeafWidth            592
TillersPerPlant           101
StemDiameterLower         101
StemDiameterUpper         101
RachisLength              443
RachisDiameterLower       443
RachisDiameterUpper       443
PrimaryBranchNo           443
BranchInternodeLength     443
dtype: int64

In [44]:
#select only PlotID, SorghumAccessing Treatment and PanickleGrainWeight column
yld = yld [['PlotIDRed','PlotIDYellow','SorghumAccessionRed','SorghumAccessionYellow','Treatment',
            'PanicleGrainWeight','DaysToBloom','PlantHeight']]
yld.head(3)

PlotIDRed  PlotIDYellow SorghumAccessionRed SorghumAccessionYellow  \
0     8390.0          9844           PI 655998              PI 655998   
1     8377.0          8390              BTx623              PI 564163   
2     8364.0          8377           PI 576396              PI 576396   

            Treatment  PanicleGrainWeight  DaysToBloom  PlantHeight  
0  SufficientNitrogen                20.0         62.0         86.0  
1  SufficientNitrogen                 NaN         65.0        102.0  
2  SufficientNitrogen                38.0         64.0         90.0

In [45]:
#rename Sorghumacessing to PI and PanicleGrainWeight to yield
yld.rename(columns = {"SorghumAccessionRed":"PIRed",
                      "SorghumAccessionYellow":"PIYellow",
                      "PanicleGrainWeight":"yield",
                      "PlotIDRed":"PlotIDRed",
                     "PlotIDYellow":"PlotIDYellow"},inplace=True)
yld.head(3)

PlotIDRed  PlotIDYellow      PIRed   PIYellow           Treatment  yield  \
0     8390.0          9844  PI 655998  PI 655998  SufficientNitrogen   20.0   
1     8377.0          8390     BTx623  PI 564163  SufficientNitrogen    NaN   
2     8364.0          8377  PI 576396  PI 576396  SufficientNitrogen   38.0   

   DaysToBloom  PlantHeight  
0         62.0         86.0  
1         65.0        102.0  
2         64.0         90.0

In [46]:
#treatments
yld.Treatment.unique()

array(['SufficientNitrogen', 'LowNitrogen'], dtype=object)

In [47]:
#change treatments labels
#LowNitrogen => LN
#SufficientNitrogen => SN

yld['Treatment'] = yld.Treatment.apply(lambda x: "HN" if x =="SufficientNitrogen" else "LN")
yld.head(3)

PlotIDRed  PlotIDYellow      PIRed   PIYellow Treatment  yield  \
0     8390.0          9844  PI 655998  PI 655998        HN   20.0   
1     8377.0          8390     BTx623  PI 564163        HN    NaN   
2     8364.0          8377  PI 576396  PI 576396        HN   38.0   

   DaysToBloom  PlantHeight  
0         62.0         86.0  
1         65.0        102.0  
2         64.0         90.0

In [48]:
yld.shape

(1848, 8)

In [49]:
yld.Treatment.value_counts()

HN    1110
LN     738
Name: Treatment, dtype: int64

In [50]:
#count nan on PlotID columns
yld.PlotIDYellow.isna().sum()

0

In [51]:
#drop nan
yld = yld[~yld.PlotIDRed.isnull()]

In [52]:
#round PlotID to nearest integer
import math
a = float('nan')
yld['PlotIDRed'] = yld.PlotIDRed.apply(lambda x: int(x))
yld.head()

PlotIDRed  PlotIDYellow      PIRed   PIYellow Treatment  yield  \
0       8390          9844  PI 655998  PI 655998        HN   20.0   
1       8377          8390     BTx623  PI 564163        HN    NaN   
2       8364          8377  PI 576396  PI 576396        HN   38.0   
3       8351          8364  PI 656023  PI 656023        HN   22.4   
4       8338          8351  PI 642992  PI 642992        HN    NaN   

   DaysToBloom  PlantHeight  
0         62.0         86.0  
1         65.0        102.0  
2         64.0         90.0  
3         73.0        150.0  
4         74.0        102.0

In [53]:
#missing value report from yield data
yld.shape #there is a total of 1944 records

(1842, 8)

In [54]:
#count by treatment
yld.Treatment.value_counts()

HN    1104
LN     738
Name: Treatment, dtype: int64

In [55]:
print(yld['yield'].isna().sum())
yld[yld['yield'].isna()].Treatment.value_counts()

325


LN    171
HN    154
Name: Treatment, dtype: int64

In [56]:
#fill-in missing values with 0 on the yield data
#yld['yield'].fillna(0,inplace = True) #dropna 
yld = yld[~yld['yield'].isnull()]
yld.shape

(1517, 8)

In [57]:
yld.Treatment.value_counts()

HN    950
LN    567
Name: Treatment, dtype: int64

In [58]:
#make a dictionary of PI and treatment and yield
#yield_data = {pi:(x,y) for pi,x,y in zip(list(yld.PI),list(yld.Treatment),list(yld['yield']))}

In [59]:
yld.isnull().sum()

PlotIDRed         0
PlotIDYellow      0
PIRed             0
PIYellow          1
Treatment         0
yield             0
DaysToBloom      15
PlantHeight     318
dtype: int64

In [60]:
#yield_data_na = yld[yld.PI.isna()]
#yield_data_na

In [61]:
#dropna from yield data
yld.dropna(axis =0, inplace = True)

## Reflectance Data

In [62]:
#import yield data
spectra = pd.read_csv('../data/Sorghum_Hyperspectral_Data.csv')
spectra.head(3)

/Users/anishimwe2/anaconda3/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3165: DtypeWarning: Columns (1) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


crop PlotID  year         trt pheno      CHL       EWT       LWC  \
0  sorghum    281  2018  greenhouse   yes  446.944  0.021140  0.801818   
1  sorghum    282  2018  greenhouse   yes  713.800  0.013651  0.718788   
2  sorghum    283  2018  greenhouse   yes  724.911  0.013870  0.715429   

          SLA     N     P     K    Mg    Ca     S     Fe     Mn     B    Cu  \
0  191.380472  2.84  0.49  2.69  0.20  0.15  0.22  133.0   27.0  12.0  13.0   
1  187.244828  3.44  0.53  2.08  0.32  1.15  0.21  109.0   98.0  38.0   9.0   
2  181.260442  3.52  0.56  1.69  0.35  1.27  0.21  113.0  147.0  36.0   9.0   

     Zn      X350      X351      X352      X353      X354      X355      X356  \
0  37.0  0.142908  0.147872  0.131849  0.096525  0.058579  0.073648  0.090709   
1  64.0  0.144607  0.133411  0.127014  0.108473  0.062686  0.078634  0.097572   
2  62.0  0.133118  0.133659  0.129053  0.105945  0.059058  0.078518  0.098973   

       X357      X358      X359      X360      X361      X362      X363  \
0  0.091497  0.089564  0.073065  0.068222  0.080974  0.084464  0.087580   
1  0.098717  0.099297  0.075012  0.071114  0.095011  0.091853  0.087312   
2  0.097981  0.095278  0.070518  0.067381  0.092476  0.092793  0.086446   

       X364      X365      X366      X367      X368      X369      X370  \
0  0.080229  0.064086  0.083023  0.091025  0.085190  0.079682  0.092441   
1  0.077852  0.064859  0.081847  0.086992  0.082989  0.085961  0.098889   
2  0.076895  0.069685  0.087265  0.089406  0.083186  0.087562  0.096989   

       X371      X372      X373      X374      X375      X376      X377  \
0  0.086188  0.065738  0.063204  0.066281  0.073109  0.077155  0.065119   
1  0.090233  0.069327  0.070434  0.075417  0.078228  0.076858  0.072080   
2  0.086667  0.066244  0.066209  0.071976  0.076505  0.076258  0.070422   

       X378      X379      X380      X381      X382      X383      X384  \
0  0.068713  0.074253  0.069952  0.071280  0.067743  0.064909  0.069064   
1  0.076396  0.078304  0.071591  0.074719  0.073626  0.070162  0.069692   
2  0.073642  0.075110  0.068252  0.069625  0.065444  0.062526  0.068870   

       X385      X386      X387      X388      X389      X390      X391  \
0  0.062337  0.063613  0.070386  0.066614  0.067137  0.071195  0.074272   
1  0.065991  0.068167  0.073365  0.071653  0.072162  0.074712  0.076154   
2  0.062721  0.064474  0.072066  0.068888  0.068324  0.070374  0.072274   

       X392      X393      X394      X395      X396      X397      X398  \
0  0.069974  0.068177  0.067990  0.067076  0.065771  0.069722  0.073364   
1  0.071298  0.071318  0.071446  0.067839  0.068895  0.072668  0.075067   
2  0.070088  0.067754  0.066173  0.065423  0.065095  0.069236  0.072735   

       X399      X400      X401      X402      X403      X404      X405  \
0  0.069445  0.065306  0.065402  0.068221  0.068122  0.069550  0.070833   
1  0.072547  0.067586  0.067888  0.071296  0.068660  0.069635  0.072082   
2  0.069307  0.065058  0.064915  0.067179  0.065646  0.066940  0.069100   

       X406      X407      X408      X409      X410      X411      X412  \
0  0.070859  0.070629  0.071852  0.072408  0.070876  0.071275  0.071306   
1  0.072835  0.069704  0.070873  0.073089  0.072369  0.072776  0.073111   
2  0.069834  0.068238  0.068724  0.069210  0.067783  0.068870  0.069666   

       X413      X414      X415      X416      X417      X418      X419  \
0  0.070232  0.068640  0.069769  0.070692  0.070718  0.071919  0.073305   
1  0.071973  0.068971  0.070703  0.071893  0.070910  0.070876  0.072144   
2  0.068674  0.066111  0.068287  0.069397  0.068036  0.068288  0.070305   

       X420      X421      X422      X423      X424      X425      X426  \
0  0.072214  0.068908  0.070574  0.072576  0.072232  0.069378  0.072004   
1  0.071891  0.069606  0.071006  0.073501  0.073903  0.070782  0.071337   
2  0.070104  0.066760  0.067481  0.069210  0.069176  0.066448  0.068050   

       X427      X428      X429      X430      X431      

In [63]:
spectra[list(spectra.columns)[:5]].info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1791 entries, 0 to 1790
Data columns (total 5 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   crop    1791 non-null   object
 1   PlotID  1791 non-null   object
 2   year    1791 non-null   int64 
 3   trt     1791 non-null   object
 4   pheno   1791 non-null   object
dtypes: int64(1), object(4)
memory usage: 70.1+ KB


In [64]:
#mport metadata for spectra data
meta = pd.read_csv('../data/Sorghum_Field_Map_2020.csv')
meta.head(3)

PlotID  Asseccion  Block Trt
0    5001  PI 656057      5  HN
1    5002  PI 656011      5  HN
2    5003  PI 576347      5  HN

In [65]:
#change plotID to object 
meta.PlotID = meta.PlotID.astype('object')

In [66]:
#join spectra data and metadata
ref = spectra.merge(meta,left_on = ['PlotID','trt'], right_on  = ['PlotID','Trt'],how = 'left')
ref.head()

crop PlotID  year         trt pheno      CHL       EWT       LWC  \
0  sorghum    281  2018  greenhouse   yes  446.944  0.021140  0.801818   
1  sorghum    282  2018  greenhouse   yes  713.800  0.013651  0.718788   
2  sorghum    283  2018  greenhouse   yes  724.911  0.013870  0.715429   
3  sorghum    284  2018  greenhouse   yes  738.400  0.016723  0.753034   
4  sorghum    285  2018  greenhouse   yes  700.344  0.023406  0.798125   

          SLA     N     P     K    Mg    Ca     S     Fe     Mn     B    Cu  \
0  191.380472  2.84  0.49  2.69  0.20  0.15  0.22  133.0   27.0  12.0  13.0   
1  187.244828  3.44  0.53  2.08  0.32  1.15  0.21  109.0   98.0  38.0   9.0   
2  181.260442  3.52  0.56  1.69  0.35  1.27  0.21  113.0  147.0  36.0   9.0   
3  182.327753  4.13  0.54  1.67  0.45  0.93  0.25  121.0  131.0  12.0  12.0   
4  168.909288  3.85  0.53  2.86  0.45  0.81  0.21  109.0   73.0  18.0   9.0   

     Zn      X350      X351      X352      X353      X354      X355      X356  \
0  37.0  0.142908  0.147872  0.131849  0.096525  0.058579  0.073648  0.090709   
1  64.0  0.144607  0.133411  0.127014  0.108473  0.062686  0.078634  0.097572   
2  62.0  0.133118  0.133659  0.129053  0.105945  0.059058  0.078518  0.098973   
3  41.0  0.123489  0.127510  0.111032  0.078294  0.053979  0.068569  0.089051   
4  31.0  0.135593  0.133549  0.121971  0.097476  0.067084  0.070520  0.089486   

       X357      X358      X359      X360      X361      X362      X363  \
0  0.091497  0.089564  0.073065  0.068222  0.080974  0.084464  0.087580   
1  0.098717  0.099297  0.075012  0.071114  0.095011  0.091853  0.087312   
2  0.097981  0.095278  0.070518  0.067381  0.092476  0.092793  0.086446   
3  0.098089  0.094430  0.070603  0.066607  0.089956  0.098283  0.092243   
4  0.103948  0.098832  0.074803  0.072382  0.094624  0.088726  0.086227   

       X364      X365      X366      X367      X368      X369      X370  \
0  0.080229  0.064086  0.083023  0.091025  0.085190  0.079682  0.092441   
1  0.077852  0.064859  0.081847  0.086992  0.082989  0.085961  0.098889   
2  0.076895  0.069685  0.087265  0.089406  0.083186  0.087562  0.096989   
3  0.075616  0.059941  0.077661  0.084944  0.083107  0.086413  0.091374   
4  0.077474  0.060286  0.077514  0.086978  0.086499  0.087641  0.096859   

       X371      X372      X373      X374      X375      X376      X377  \
0  0.086188  0.065738  0.063204  0.066281  0.073109  0.077155  0.065119   
1  0.090233  0.069327  0.070434  0.075417  0.078228  0.076858  0.072080   
2  0.086667  0.066244  0.066209  0.071976  0.076505  0.076258  0.070422   
3  0.081638  0.065212  0.064903  0.070860  0.076368  0.076411  0.067212   
4  0.089147  0.071181  0.069390  0.070741  0.072909  0.073936  0.070862   

       X378      X379      X380      X381      X382      X383      X384  \
0  0.068713  0.074253  0.069952  0.071280  0.067743  0.064909  0.069064   
1  0.076396  0.078304  0.071591  0.074719  0.073626  0.070162  0.069692   
2  0.073642  0.075110  0.068252  0.069625  0.065444  0.062526  0.068870   
3  0.071461  0.076470  0.072169  0.072288  0.068967  0.065652  0.066930   
4  0.075020  0.077396  0.072526  0.073401  0.069893  0.066800  0.069752   

       X385      X386      X387      X388      X389      X390      X391  \
0  0.062337  0.063613  0.070386  0.066614  0.067137  0.071195  0.074272   
1  0.065991  0.068167  0.073365  0.071653  0.072162  0.074712  0.076154   
2  0.062721  0.064474  0.072066  0.068888  0.068324  0.070374  0.072274   
3  0.063062  0.065132  0.070059  0.066485  0.067889  0.070382  0.070372   
4  0.061828  0.065238  0.075241  0.070553  0.070236  0.073345  0.075085   

       X392      X393      X394      X395      X396      X397      X398  \
0  0.069974  0.068177  0.067990  0.067076  0.065771  0.069722  0.073364   
1  0.071298  0.071318  0.071446  0.067839  0.068895  0.072668  0.075067   
2  0.070088  0.067754  0.066173  0.065423  0.065095  0.069236  0.072735   
3  0.067653  0.067147  0.066566  0.064307  0

In [67]:
ref.shape

(1791, 2174)

In [68]:
ref.trt.value_counts()

HN            738
LN            732
greenhouse    321
Name: trt, dtype: int64

In [69]:
#filer out those with no accessig and not Trt
ref = ref[(~ref.Asseccion.isna()) |(~ref.Trt.isna())]
ref[['crop','PlotID','year','trt','Trt','Asseccion']].head()

crop PlotID  year trt Trt  Asseccion
321  sorghum   5001  2020  HN  HN  PI 656057
322  sorghum   5002  2020  HN  HN  PI 656011
323  sorghum   5003  2020  HN  HN  PI 576347
328  sorghum   5008  2020  HN  HN  PI 533876
329  sorghum   5009  2020  HN  HN     BTx623

In [70]:
#check the shape of our reflectance data
ref.shape

(920, 2174)

In [71]:
ref.trt.value_counts()

LN    573
HN    347
Name: trt, dtype: int64

In [72]:
#wavelengths
pchem = list(ref.columns)[5:20]
waves = [x for x in list(ref.columns) if x.startswith('X')]
ref = ref[['PlotID','trt','Asseccion']+pchem +waves]
ref.head()

PlotID trt  Asseccion       CHL       EWT       LWC        SLA      N  \
321   5001  HN  PI 656057  467.6750  0.048621  0.816438  91.477861  3.612   
322   5002  HN  PI 656011  512.3625  0.043236  0.768144  76.626487  2.916   
323   5003  HN  PI 576347  606.6625  0.033848  0.751805  89.492182  3.749   
328   5008  HN  PI 533876  657.4500  0.034768  0.749633  86.117025  3.247   
329   5009  HN     BTx623  606.9375  0.040890  0.748609  72.826292  3.333   

         P     K     Mg     Ca      S     Fe    Mn    B    Cu    Zn      X350  \
321  0.381  1.93  0.245  0.674  0.206  171.0  31.0  6.4  17.6  28.0  0.085242   
322  0.387  2.24  0.143  0.447  0.196  134.0  34.0  4.6  12.5  27.0  0.053529   
323  0.492  1.54  0.260  0.583  0.196  159.0  36.0  5.1  15.4  32.0  0.133649   
328  0.435  2.43  0.182  0.379  0.181  161.0  20.0  3.6   9.3  37.0  0.097695   
329  0.405  1.74  0.215  0.416  0.193  177.0  36.0  5.7  15.8  36.0  0.094066   

         X351      X352      X353      X354      X355      X356      X357  \
321  0.084198  0.073049  0.062852  0.071412  0.076959  0.086402  0.089655   
322  0.087761  0.089831  0.066536  0.070464  0.065440  0.057905  0.061879   
323  0.113164  0.095398  0.095292  0.097985  0.089531  0.085457  0.086694   
328  0.118079  0.092867  0.050600  0.070654  0.073108  0.083471  0.096579   
329  0.106925  0.082118  0.048393  0.083301  0.093091  0.088455  0.080103   

         X358      X359      X360      X361      X362      X363      X364  \
321  0.068680  0.077627  0.075629  0.049378  0.047664  0.048732  0.053430   
322  0.087529  0.083688  0.066741  0.054267  0.042131  0.050978  0.056994   
323  0.082119  0.090674  0.082183  0.057630  0.074017  0.063699  0.056483   
328  0.079057  0.080954  0.085262  0.081199  0.082543  0.074632  0.065478   
329  0.072284  0.066456  0.063065  0.062131  0.066061  0.068730  0.061228   

         X365      X366      X367      X368      X369      X370      X371  \
321  0.059725  0.043177  0.055788  0.069612  0.049814  0.054452  0.055179   
322  0.045107  0.046368  0.043490  0.042569  0.050927  0.046258  0.041853   
323  0.072555  0.051468  0.052361  0.063759  0.055830  0.039474  0.044329   
328  0.063047  0.060183  0.055471  0.053983  0.059142  0.054930  0.057955   
329  0.046188  0.058221  0.063865  0.057511  0.047299  0.053168  0.055891   

         X372      X373      X374      X375      X376      X377      X378  \
321  0.045720  0.038621  0.047542  0.053812  0.049443  0.042255  0.043361   
322  0.043365  0.048262  0.047062  0.048264  0.051650  0.044692  0.043194   
323  0.059886  0.055076  0.055611  0.054215  0.045810  0.032091  0.028689   
328  0.061974  0.048927  0.050197  0.052943  0.051500  0.054705  0.054921   
329  0.053667  0.055631  0.047835  0.044321  0.048670  0.048353  0.047006   

         X379      X380      X381      X382      X383      X384      X385  \
321  0.048633  0.051029  0.044424  0.043408  0.041854  0.032599  0.041451   
322  0.040966  0.035022  0.041995  0.044352  0.042166  0.041462  0.043841   
323  0.033169  0.038722  0.042077  0.040161  0.037917  0.041208  0.046213   
328  0.048870  0.038668  0.036536  0.038733  0.041367  0.041484  0.040008   
329  0.045872  0.046358  0.052539  0.049135  0.044182  0.048988  0.048012   

         X386      X387      X388      X389      X390      X391      X392  \
321  0.048299  0.048850  0.050056  0.046709  0.043648  0.042465  0.038687   
322  0.043980  0.042063  0.041588  0.038251  0.035009  0.034469  0.037531   
323  0.048145  0.046461  0.043884  0.043052  0.039607  0.035373  0.041091   
328  0.042213  0.045475  0.042903  0.041452  0.041014  0.040350  0.037966   
329  0.048512  0.051255  0.052092  0.051083  0.049982  0.048607  0.043893   

         X393      X394      X395      X396      X397      X398      X399  \
321  0.046113  0.051060  0.044858  0.047175  0.049994  0.049110  0.043823   
322  0.040736  0.042420  0.042195  0.041240  0.040235  0.039823  0.040379   
323  0.045182  0.045669  0.043754  0.042794  

In [75]:
#rename trt to Treatment
ref.rename(columns={'trt':"Treatment",'Asseccion':'PI'},inplace = True)
ref.head(3)

PlotID Treatment         PI       CHL       EWT       LWC        SLA  \
321   5001        HN  PI 656057  467.6750  0.048621  0.816438  91.477861   
322   5002        HN  PI 656011  512.3625  0.043236  0.768144  76.626487   
323   5003        HN  PI 576347  606.6625  0.033848  0.751805  89.492182   

         N      P     K     Mg     Ca      S     Fe    Mn    B    Cu    Zn  \
321  3.612  0.381  1.93  0.245  0.674  0.206  171.0  31.0  6.4  17.6  28.0   
322  2.916  0.387  2.24  0.143  0.447  0.196  134.0  34.0  4.6  12.5  27.0   
323  3.749  0.492  1.54  0.260  0.583  0.196  159.0  36.0  5.1  15.4  32.0   

         X350      X351      X352      X353      X354      X355      X356  \
321  0.085242  0.084198  0.073049  0.062852  0.071412  0.076959  0.086402   
322  0.053529  0.087761  0.089831  0.066536  0.070464  0.065440  0.057905   
323  0.133649  0.113164  0.095398  0.095292  0.097985  0.089531  0.085457   

         X357      X358      X359      X360      X361      X362      X363  \
321  0.089655  0.068680  0.077627  0.075629  0.049378  0.047664  0.048732   
322  0.061879  0.087529  0.083688  0.066741  0.054267  0.042131  0.050978   
323  0.086694  0.082119  0.090674  0.082183  0.057630  0.074017  0.063699   

         X364      X365      X366      X367      X368      X369      X370  \
321  0.053430  0.059725  0.043177  0.055788  0.069612  0.049814  0.054452   
322  0.056994  0.045107  0.046368  0.043490  0.042569  0.050927  0.046258   
323  0.056483  0.072555  0.051468  0.052361  0.063759  0.055830  0.039474   

         X371      X372      X373      X374      X375      X376      X377  \
321  0.055179  0.045720  0.038621  0.047542  0.053812  0.049443  0.042255   
322  0.041853  0.043365  0.048262  0.047062  0.048264  0.051650  0.044692   
323  0.044329  0.059886  0.055076  0.055611  0.054215  0.045810  0.032091   

         X378      X379      X380      X381      X382      X383      X384  \
321  0.043361  0.048633  0.051029  0.044424  0.043408  0.041854  0.032599   
322  0.043194  0.040966  0.035022  0.041995  0.044352  0.042166  0.041462   
323  0.028689  0.033169  0.038722  0.042077  0.040161  0.037917  0.041208   

         X385      X386      X387      X388      X389      X390      X391  \
321  0.041451  0.048299  0.048850  0.050056  0.046709  0.043648  0.042465   
322  0.043841  0.043980  0.042063  0.041588  0.038251  0.035009  0.034469   
323  0.046213  0.048145  0.046461  0.043884  0.043052  0.039607  0.035373   

         X392      X393      X394      X395      X396      X397      X398  \
321  0.038687  0.046113  0.051060  0.044858  0.047175  0.049994  0.049110   
322  0.037531  0.040736  0.042420  0.042195  0.041240  0.040235  0.039823   
323  0.041091  0.045182  0.045669  0.043754  0.042794  0.041254  0.040067   

         X399      X400      X401      X402      X403      X404      X405  \
321  0.043823  0.043862  0.041952  0.039572  0.044624  0.044988  0.046128   
322  0.040379  0.041654  0.042781  0.042810  0.041331  0.044993  0.048847   
323  0.040752  0.043151  0.043261  0.042180  0.044544  0.044126  0.043205   

         X406      X407      X408      X409      X410      X411      X412  \
321  0.048967  0.043201  0.043568  0.048380  0.051787  0.049475  0.048316   
322  0.048443  0.042648  0.044995  0.048170  0.044979  0.047369  0.049684   
323  0.043584  0.044392  0.045137  0.045063  0.044390  0.046864  0.045013   

         X413      X414      X415      X416      X417      X418      X419  \
321  0.046960  0.041976  0.046816  0.049948  0.048506  0.050128  0.048849   
322  0.049955  0.048659  0.048421  0.048269  0.048416  0.050394  0.048258   
323  0.043726  0.050980  0.051151  0.049499  0.049354  0.050059  0.049096   

         X420      X421      X422      X423      X424      X425      X426  \
321  0.048119  0.050257  0.051968  0.050424  0.047950  0.047706  0.047331   
322  0.048416  0.052975  0.049087  0.050950  0.054511  0.052481  0.052212   
323  0.048275  0.048961  0.049973  0.049505  0.048687  0.049145  

## Join Yield Data and Reflectance Data

In [34]:
yld.head()

PlotIDRed  PlotIDYellow      PIRed   PIYellow Treatment  yield  \
0       8390          9844  PI 655998  PI 655998        HN   20.0   
2       8364          8377  PI 576396  PI 576396        HN   38.0   
3       8351          8364  PI 656023  PI 656023        HN   22.4   
6       8312          8325  PI 534128  PI 534128        HN    2.4   
7       8299          8312  PI 576418  PI 576418        HN   29.7   

   DaysToBloom  PlantHeight  
0         62.0         86.0  
2         64.0         90.0  
3         73.0        150.0  
6         71.0        102.0  
7         67.0        120.0

In [77]:
#create yld_red dataframe
yld_red = yld.copy() 
yld_red.drop(['PlotIDYellow','PIYellow'], axis = 1, inplace = True)
yld_red.rename(columns = {"PlotIDRed":"PlotID", "PIRed":"PI"}, inplace = True)

In [79]:
yld_red.head(3)

PlotID         PI Treatment  yield  DaysToBloom  PlantHeight
0    8390  PI 655998        HN   20.0         62.0         86.0
2    8364  PI 576396        HN   38.0         64.0         90.0
3    8351  PI 656023        HN   22.4         73.0        150.0

In [78]:
#create yld_yel dataframe
yld_yellow = yld.copy() 
yld_yellow.drop(['PlotIDRed','PIRed'], axis = 1, inplace = True)
yld_yellow.rename(columns = {"PlotIDYellow":"PlotID", "PIYellow":"PI"}, inplace = True)

In [80]:
yld_yellow.head(3)

PlotID         PI Treatment  yield  DaysToBloom  PlantHeight
0    9844  PI 655998        HN   20.0         62.0         86.0
2    8377  PI 576396        HN   38.0         64.0         90.0
3    8364  PI 656023        HN   22.4         73.0        150.0

### PlotIDYellow for Imputataion and PlotIDRed for joining to reflectance data

In [81]:
#Inner join of yield data and reflectance data based on PlotID, Treatment and PI
#Merge on the red bands
df = ref.merge(yld_red,on=['PlotID'], how = 'left', suffixes = ["","_y"])
df.head()


PlotID Treatment         PI       CHL       EWT       LWC        SLA      N  \
0   5001        HN  PI 656057  467.6750  0.048621  0.816438  91.477861  3.612   
1   5002        HN  PI 656011  512.3625  0.043236  0.768144  76.626487  2.916   
2   5003        HN  PI 576347  606.6625  0.033848  0.751805  89.492182  3.749   
3   5008        HN  PI 533876  657.4500  0.034768  0.749633  86.117025  3.247   
4   5009        HN     BTx623  606.9375  0.040890  0.748609  72.826292  3.333   

       P     K     Mg     Ca      S     Fe    Mn    B    Cu    Zn      X350  \
0  0.381  1.93  0.245  0.674  0.206  171.0  31.0  6.4  17.6  28.0  0.085242   
1  0.387  2.24  0.143  0.447  0.196  134.0  34.0  4.6  12.5  27.0  0.053529   
2  0.492  1.54  0.260  0.583  0.196  159.0  36.0  5.1  15.4  32.0  0.133649   
3  0.435  2.43  0.182  0.379  0.181  161.0  20.0  3.6   9.3  37.0  0.097695   
4  0.405  1.74  0.215  0.416  0.193  177.0  36.0  5.7  15.8  36.0  0.094066   

       X351      X352      X353      X354      X355      X356      X357  \
0  0.084198  0.073049  0.062852  0.071412  0.076959  0.086402  0.089655   
1  0.087761  0.089831  0.066536  0.070464  0.065440  0.057905  0.061879   
2  0.113164  0.095398  0.095292  0.097985  0.089531  0.085457  0.086694   
3  0.118079  0.092867  0.050600  0.070654  0.073108  0.083471  0.096579   
4  0.106925  0.082118  0.048393  0.083301  0.093091  0.088455  0.080103   

       X358      X359      X360      X361      X362      X363      X364  \
0  0.068680  0.077627  0.075629  0.049378  0.047664  0.048732  0.053430   
1  0.087529  0.083688  0.066741  0.054267  0.042131  0.050978  0.056994   
2  0.082119  0.090674  0.082183  0.057630  0.074017  0.063699  0.056483   
3  0.079057  0.080954  0.085262  0.081199  0.082543  0.074632  0.065478   
4  0.072284  0.066456  0.063065  0.062131  0.066061  0.068730  0.061228   

       X365      X366      X367      X368      X369      X370      X371  \
0  0.059725  0.043177  0.055788  0.069612  0.049814  0.054452  0.055179   
1  0.045107  0.046368  0.043490  0.042569  0.050927  0.046258  0.041853   
2  0.072555  0.051468  0.052361  0.063759  0.055830  0.039474  0.044329   
3  0.063047  0.060183  0.055471  0.053983  0.059142  0.054930  0.057955   
4  0.046188  0.058221  0.063865  0.057511  0.047299  0.053168  0.055891   

       X372      X373      X374      X375      X376      X377      X378  \
0  0.045720  0.038621  0.047542  0.053812  0.049443  0.042255  0.043361   
1  0.043365  0.048262  0.047062  0.048264  0.051650  0.044692  0.043194   
2  0.059886  0.055076  0.055611  0.054215  0.045810  0.032091  0.028689   
3  0.061974  0.048927  0.050197  0.052943  0.051500  0.054705  0.054921   
4  0.053667  0.055631  0.047835  0.044321  0.048670  0.048353  0.047006   

       X379      X380      X381      X382      X383      X384      X385  \
0  0.048633  0.051029  0.044424  0.043408  0.041854  0.032599  0.041451   
1  0.040966  0.035022  0.041995  0.044352  0.042166  0.041462  0.043841   
2  0.033169  0.038722  0.042077  0.040161  0.037917  0.041208  0.046213   
3  0.048870  0.038668  0.036536  0.038733  0.041367  0.041484  0.040008   
4  0.045872  0.046358  0.052539  0.049135  0.044182  0.048988  0.048012   

       X386      X387      X388      X389      X390      X391      X392  \
0  0.048299  0.048850  0.050056  0.046709  0.043648  0.042465  0.038687   
1  0.043980  0.042063  0.041588  0.038251  0.035009  0.034469  0.037531   
2  0.048145  0.046461  0.043884  0.043052  0.039607  0.035373  0.041091   
3  0.042213  0.045475  0.042903  0.041452  0.041014  0.040350  0.037966   
4  0.048512  0.051255  0.052092  0.051083  0.049982  0.048607  0.043893   

       X393      X394      X395      X396      X397      X398      X399  \
0  0.046113  0.051060  0.044858  0.047175  0.049994  0.049110  0.043823   
1  0.040736  0.042420  0.042195  0.041240  0.040235  0.039823  0.040379   
2  0.045182  0.045669  0.043754  0.042794  0.041254  0.040067  0.040752   
3  0.038778  0.039216  0.037530  0

In [83]:
df.drop(['PI_y','Treatment_y'], axis = 1, inplace = True)
df.head(3)

PlotID Treatment         PI       CHL       EWT       LWC        SLA      N  \
0   5001        HN  PI 656057  467.6750  0.048621  0.816438  91.477861  3.612   
1   5002        HN  PI 656011  512.3625  0.043236  0.768144  76.626487  2.916   
2   5003        HN  PI 576347  606.6625  0.033848  0.751805  89.492182  3.749   

       P     K     Mg     Ca      S     Fe    Mn    B    Cu    Zn      X350  \
0  0.381  1.93  0.245  0.674  0.206  171.0  31.0  6.4  17.6  28.0  0.085242   
1  0.387  2.24  0.143  0.447  0.196  134.0  34.0  4.6  12.5  27.0  0.053529   
2  0.492  1.54  0.260  0.583  0.196  159.0  36.0  5.1  15.4  32.0  0.133649   

       X351      X352      X353      X354      X355      X356      X357  \
0  0.084198  0.073049  0.062852  0.071412  0.076959  0.086402  0.089655   
1  0.087761  0.089831  0.066536  0.070464  0.065440  0.057905  0.061879   
2  0.113164  0.095398  0.095292  0.097985  0.089531  0.085457  0.086694   

       X358      X359      X360      X361      X362      X363      X364  \
0  0.068680  0.077627  0.075629  0.049378  0.047664  0.048732  0.053430   
1  0.087529  0.083688  0.066741  0.054267  0.042131  0.050978  0.056994   
2  0.082119  0.090674  0.082183  0.057630  0.074017  0.063699  0.056483   

       X365      X366      X367      X368      X369      X370      X371  \
0  0.059725  0.043177  0.055788  0.069612  0.049814  0.054452  0.055179   
1  0.045107  0.046368  0.043490  0.042569  0.050927  0.046258  0.041853   
2  0.072555  0.051468  0.052361  0.063759  0.055830  0.039474  0.044329   

       X372      X373      X374      X375      X376      X377      X378  \
0  0.045720  0.038621  0.047542  0.053812  0.049443  0.042255  0.043361   
1  0.043365  0.048262  0.047062  0.048264  0.051650  0.044692  0.043194   
2  0.059886  0.055076  0.055611  0.054215  0.045810  0.032091  0.028689   

       X379      X380      X381      X382      X383      X384      X385  \
0  0.048633  0.051029  0.044424  0.043408  0.041854  0.032599  0.041451   
1  0.040966  0.035022  0.041995  0.044352  0.042166  0.041462  0.043841   
2  0.033169  0.038722  0.042077  0.040161  0.037917  0.041208  0.046213   

       X386      X387      X388      X389      X390      X391      X392  \
0  0.048299  0.048850  0.050056  0.046709  0.043648  0.042465  0.038687   
1  0.043980  0.042063  0.041588  0.038251  0.035009  0.034469  0.037531   
2  0.048145  0.046461  0.043884  0.043052  0.039607  0.035373  0.041091   

       X393      X394      X395      X396      X397      X398      X399  \
0  0.046113  0.051060  0.044858  0.047175  0.049994  0.049110  0.043823   
1  0.040736  0.042420  0.042195  0.041240  0.040235  0.039823  0.040379   
2  0.045182  0.045669  0.043754  0.042794  0.041254  0.040067  0.040752   

       X400      X401      X402      X403      X404      X405      X406  \
0  0.043862  0.041952  0.039572  0.044624  0.044988  0.046128  0.048967   
1  0.041654  0.042781  0.042810  0.041331  0.044993  0.048847  0.048443   
2  0.043151  0.043261  0.042180  0.044544  0.044126  0.043205  0.043584   

       X407      X408      X409      X410      X411      X412      X413  \
0  0.043201  0.043568  0.048380  0.051787  0.049475  0.048316  0.046960   
1  0.042648  0.044995  0.048170  0.044979  0.047369  0.049684  0.049955   
2  0.044392  0.045137  0.045063  0.044390  0.046864  0.045013  0.043726   

       X414      X415      X416      X417      X418      X419      X420  \
0  0.041976  0.046816  0.049948  0.048506  0.050128  0.048849  0.048119   
1  0.048659  0.048421  0.048269  0.048416  0.050394  0.048258  0.048416   
2  0.050980  0.051151  0.049499  0.049354  0.050059  0.049096  0.048275   

       X421      X422      X423      X424      X425      X426      X427  \
0  0.050257  0.051968  0.050424  0.047950  0.047706  0.047331  0.047042   
1  0.052975  0.049087  0.050950  0.054511  0.052481  0.052212  0.052104   
2  0.048961  0.049973  0.049505  0.048687  0.049145  0.049398  0.051126   

       X428      X429      X430      X431      X4

In [84]:
df.set_index('PlotID', inplace = True)
yld_yellow_copy = yld_yellow.copy()
yld_yellow_copy.set_index('PlotID',inplace = True)
df.head(3)

Treatment         PI       CHL       EWT       LWC        SLA      N  \
PlotID                                                                        
5001          HN  PI 656057  467.6750  0.048621  0.816438  91.477861  3.612   
5002          HN  PI 656011  512.3625  0.043236  0.768144  76.626487  2.916   
5003          HN  PI 576347  606.6625  0.033848  0.751805  89.492182  3.749   

            P     K     Mg     Ca      S     Fe    Mn    B    Cu    Zn  \
PlotID                                                                   
5001    0.381  1.93  0.245  0.674  0.206  171.0  31.0  6.4  17.6  28.0   
5002    0.387  2.24  0.143  0.447  0.196  134.0  34.0  4.6  12.5  27.0   
5003    0.492  1.54  0.260  0.583  0.196  159.0  36.0  5.1  15.4  32.0   

            X350      X351      X352      X353      X354      X355      X356  \
PlotID                                                                         
5001    0.085242  0.084198  0.073049  0.062852  0.071412  0.076959  0.086402   
5002    0.053529  0.087761  0.089831  0.066536  0.070464  0.065440  0.057905   
5003    0.133649  0.113164  0.095398  0.095292  0.097985  0.089531  0.085457   

            X357      X358      X359      X360      X361      X362      X363  \
PlotID                                                                         
5001    0.089655  0.068680  0.077627  0.075629  0.049378  0.047664  0.048732   
5002    0.061879  0.087529  0.083688  0.066741  0.054267  0.042131  0.050978   
5003    0.086694  0.082119  0.090674  0.082183  0.057630  0.074017  0.063699   

            X364      X365      X366      X367      X368      X369      X370  \
PlotID                                                                         
5001    0.053430  0.059725  0.043177  0.055788  0.069612  0.049814  0.054452   
5002    0.056994  0.045107  0.046368  0.043490  0.042569  0.050927  0.046258   
5003    0.056483  0.072555  0.051468  0.052361  0.063759  0.055830  0.039474   

            X371      X372      X373      X374      X375      X376      X377  \
PlotID                                                                         
5001    0.055179  0.045720  0.038621  0.047542  0.053812  0.049443  0.042255   
5002    0.041853  0.043365  0.048262  0.047062  0.048264  0.051650  0.044692   
5003    0.044329  0.059886  0.055076  0.055611  0.054215  0.045810  0.032091   

            X378      X379      X380      X381      X382      X383      X384  \
PlotID                                                                         
5001    0.043361  0.048633  0.051029  0.044424  0.043408  0.041854  0.032599   
5002    0.043194  0.040966  0.035022  0.041995  0.044352  0.042166  0.041462   
5003    0.028689  0.033169  0.038722  0.042077  0.040161  0.037917  0.041208   

            X385      X386      X387      X388      X389      X390      X391  \
PlotID                                                                         
5001    0.041451  0.048299  0.048850  0.050056  0.046709  0.043648  0.042465   
5002    0.043841  0.043980  0.042063  0.041588  0.038251  0.035009  0.034469   
5003    0.046213  0.048145  0.046461  0.043884  0.043052  0.039607  0.035373   

            X392      X393      X394      X395      X396      X397      X398  \
PlotID                                                                         
5001    0.038687  0.046113  0.051060  0.044858  0.047175  0.049994  0.049110   
5002    0.037531  0.040736  0.042420  0.042195  0.041240  0.040235  0.039823   
5003    0.041091  0.045182  0.045669  0.043754  0.042794  0.041254  0.040067   

            X399      X400      X401      X402      X403      X404      X405  \
PlotID                                                                         
5001    0.043823  0.043862  0.041952  0.039572  0.044624  0.044988  0.046128   
5002    0.040379  0.041654  0.042781  0.042810  0.041331  0.044993  0.048847   
5003    0.040752  0.043151  0.043261  0.042180  0.044544  0.044126  0.043205   

            X406      X407      

In [87]:
list(yld_red.columns)

['PlotID', 'PI', 'Treatment', 'yield', 'DaysToBloom', 'PlantHeight']

In [89]:
df[['PI', 'Treatment', 'yield', 'DaysToBloom', 'PlantHeight']].isnull().sum()

PI               0
Treatment        0
yield          234
DaysToBloom    234
PlantHeight    234
dtype: int64

In [85]:
yld_yellow_copy.head(3)

PI Treatment  yield  DaysToBloom  PlantHeight
PlotID                                                      
9844    PI 655998        HN   20.0         62.0         86.0
8377    PI 576396        HN   38.0         64.0         90.0
8364    PI 656023        HN   22.4         73.0        150.0

In [97]:
#imputation
df = df.combine_first(yld_yellow_copy)


In [98]:
df[['PI', 'Treatment', 'yield', 'DaysToBloom', 'PlantHeight']].isnull().sum()

PI               0
Treatment        0
yield          103
DaysToBloom    103
PlantHeight    103
dtype: int64

In [99]:
df.shape

(1397, 2171)

In [102]:
df = df[~df['yield'].isnull()]
df.shape

(1294, 2171)

In [103]:
df.head(3)

B       CHL     Ca    Cu  DaysToBloom       EWT     Fe     K  \
PlotID                                                                   
5001    6.4  467.6750  0.674  17.6         83.0  0.048621  171.0  1.93   
5002    4.6  512.3625  0.447  12.5         76.0  0.043236  134.0  2.24   
5009    5.7  606.9375  0.416  15.8         61.0  0.040890  177.0  1.74   

             LWC     Mg    Mn      N      P         PI  PlantHeight      S  \
PlotID                                                                       
5001    0.816438  0.245  31.0  3.612  0.381  PI 656057        128.0  0.206   
5002    0.768144  0.143  34.0  2.916  0.387  PI 656011        110.0  0.196   
5009    0.748609  0.215  36.0  3.333  0.405     BTx623         62.0  0.193   

              SLA Treatment     X1000     X1001     X1002     X1003     X1004  \
PlotID                                                                          
5001    91.477861        HN  0.474277  0.474403  0.474529  0.474655  0.474781   
5002    76.626487        HN  0.491301  0.491336  0.491371  0.491406  0.491441   
5009    72.826292        HN  0.519076  0.519423  0.519770  0.520118  0.520465   

           X1005     X1006     X1007     X1008     X1009     X1010     X1011  \
PlotID                                                                         
5001    0.474907  0.475033  0.475158  0.475284  0.475410  0.475536  0.475688   
5002    0.491476  0.491511  0.491546  0.491581  0.491616  0.491651  0.491807   
5009    0.520812  0.521159  0.521506  0.521853  0.522200  0.522547  0.522712   

           X1012     X1013     X1014     X1015     X1016     X1017     X1018  \
PlotID                                                                         
5001    0.475883  0.476092  0.476295  0.476547  0.476731  0.476871  0.477020   
5002    0.491928  0.492030  0.492137  0.492215  0.492333  0.492478  0.492602   
5009    0.522885  0.523075  0.523255  0.523439  0.523596  0.523754  0.523889   

           X1019     X1020     X1021     X1022     X1023     X1024     X1025  \
PlotID                                                                         
5001    0.477147  0.477276  0.477380  0.477523  0.477682  0.477841  0.478011   
5002    0.492748  0.492863  0.492936  0.493039  0.493149  0.493257  0.493370   
5009    0.523965  0.524094  0.524232  0.524383  0.524581  0.524749  0.524909   

           X1026     X1027     X1028     X1029     X1030     X1031     X1032  \
PlotID                                                                         
5001    0.478220  0.478387  0.478526  0.478696  0.478880  0.479037  0.479199   
5002    0.493498  0.493618  0.493741  0.493842  0.493932  0.494028  0.494113   
5009    0.525081  0.525195  0.525268  0.525364  0.525423  0.525521  0.525639   

           X1033     X1034     X1035     X1036     X1037     X1038     X1039  \
PlotID                                                                         
5001    0.479345  0.479467  0.479586  0.479698  0.479813  0.479914  0.480025   
5002    0.494193  0.494277  0.494364  0.494443  0.494519  0.494613  0.494685   
5009    0.525765  0.525923  0.526042  0.526136  0.526260  0.526391  0.526501   

           X1040     X1041     X1042     X1043     X1044     X1045     X1046  \
PlotID                                                                         
5001    0.480153  0.480272  0.480370  0.480458  0.480537  0.480597  0.480662   
5002    0.494733  0.494779  0.494834  0.494890  0.494936  0.494995  0.495023   
5009    0.526616  0.526742  0.526853  0.526945  0.527013  0.527071  0.527143   

           X1047     X1048     X1049     X1050     X1051     X1052     X1053  \
PlotID                                                                         
5001    0.480722  0.480787  0.480848  0.480909  0.480994  0.481044  0.481075   
5002    0.495011  0.495038  0.495073  0.495094  0.495132  0.495155  0.495170   
5009    0.527181  0.527246  0.527363  0.527430  0.527461  0.527514  0.527558   

           X1054     X1055     X105

In [104]:
#reset index
df.reset_index(inplace = True)

In [106]:
df.to_csv('../data/data_yellow_imputed-1.2.csv')

### PlotIDRed for Imputataion and PlotIDYellow for joining to reflectance data

In [108]:
#Merge on the red bands
dff = ref.merge(yld_yellow,on=['PlotID'], how = 'left', suffixes = ["","_y"])
dff.head()


PlotID Treatment         PI       CHL       EWT       LWC        SLA      N  \
0   5001        HN  PI 656057  467.6750  0.048621  0.816438  91.477861  3.612   
1   5002        HN  PI 656011  512.3625  0.043236  0.768144  76.626487  2.916   
2   5003        HN  PI 576347  606.6625  0.033848  0.751805  89.492182  3.749   
3   5008        HN  PI 533876  657.4500  0.034768  0.749633  86.117025  3.247   
4   5009        HN     BTx623  606.9375  0.040890  0.748609  72.826292  3.333   

       P     K     Mg     Ca      S     Fe    Mn    B    Cu    Zn      X350  \
0  0.381  1.93  0.245  0.674  0.206  171.0  31.0  6.4  17.6  28.0  0.085242   
1  0.387  2.24  0.143  0.447  0.196  134.0  34.0  4.6  12.5  27.0  0.053529   
2  0.492  1.54  0.260  0.583  0.196  159.0  36.0  5.1  15.4  32.0  0.133649   
3  0.435  2.43  0.182  0.379  0.181  161.0  20.0  3.6   9.3  37.0  0.097695   
4  0.405  1.74  0.215  0.416  0.193  177.0  36.0  5.7  15.8  36.0  0.094066   

       X351      X352      X353      X354      X355      X356      X357  \
0  0.084198  0.073049  0.062852  0.071412  0.076959  0.086402  0.089655   
1  0.087761  0.089831  0.066536  0.070464  0.065440  0.057905  0.061879   
2  0.113164  0.095398  0.095292  0.097985  0.089531  0.085457  0.086694   
3  0.118079  0.092867  0.050600  0.070654  0.073108  0.083471  0.096579   
4  0.106925  0.082118  0.048393  0.083301  0.093091  0.088455  0.080103   

       X358      X359      X360      X361      X362      X363      X364  \
0  0.068680  0.077627  0.075629  0.049378  0.047664  0.048732  0.053430   
1  0.087529  0.083688  0.066741  0.054267  0.042131  0.050978  0.056994   
2  0.082119  0.090674  0.082183  0.057630  0.074017  0.063699  0.056483   
3  0.079057  0.080954  0.085262  0.081199  0.082543  0.074632  0.065478   
4  0.072284  0.066456  0.063065  0.062131  0.066061  0.068730  0.061228   

       X365      X366      X367      X368      X369      X370      X371  \
0  0.059725  0.043177  0.055788  0.069612  0.049814  0.054452  0.055179   
1  0.045107  0.046368  0.043490  0.042569  0.050927  0.046258  0.041853   
2  0.072555  0.051468  0.052361  0.063759  0.055830  0.039474  0.044329   
3  0.063047  0.060183  0.055471  0.053983  0.059142  0.054930  0.057955   
4  0.046188  0.058221  0.063865  0.057511  0.047299  0.053168  0.055891   

       X372      X373      X374      X375      X376      X377      X378  \
0  0.045720  0.038621  0.047542  0.053812  0.049443  0.042255  0.043361   
1  0.043365  0.048262  0.047062  0.048264  0.051650  0.044692  0.043194   
2  0.059886  0.055076  0.055611  0.054215  0.045810  0.032091  0.028689   
3  0.061974  0.048927  0.050197  0.052943  0.051500  0.054705  0.054921   
4  0.053667  0.055631  0.047835  0.044321  0.048670  0.048353  0.047006   

       X379      X380      X381      X382      X383      X384      X385  \
0  0.048633  0.051029  0.044424  0.043408  0.041854  0.032599  0.041451   
1  0.040966  0.035022  0.041995  0.044352  0.042166  0.041462  0.043841   
2  0.033169  0.038722  0.042077  0.040161  0.037917  0.041208  0.046213   
3  0.048870  0.038668  0.036536  0.038733  0.041367  0.041484  0.040008   
4  0.045872  0.046358  0.052539  0.049135  0.044182  0.048988  0.048012   

       X386      X387      X388      X389      X390      X391      X392  \
0  0.048299  0.048850  0.050056  0.046709  0.043648  0.042465  0.038687   
1  0.043980  0.042063  0.041588  0.038251  0.035009  0.034469  0.037531   
2  0.048145  0.046461  0.043884  0.043052  0.039607  0.035373  0.041091   
3  0.042213  0.045475  0.042903  0.041452  0.041014  0.040350  0.037966   
4  0.048512  0.051255  0.052092  0.051083  0.049982  0.048607  0.043893   

       X393      X394      X395      X396      X397      X398      X399  \
0  0.046113  0.051060  0.044858  0.047175  0.049994  0.049110  0.043823   
1  0.040736  0.042420  0.042195  0.041240  0.040235  0.039823  0.040379   
2  0.045182  0.045669  0.043754  0.042794  0.041254  0.040067  0.040752   
3  0.038778  0.039216  0.037530  0

In [109]:
dff.drop(['PI_y','Treatment_y'], axis = 1, inplace = True)
dff.head(3)

PlotID Treatment         PI       CHL       EWT       LWC        SLA      N  \
0   5001        HN  PI 656057  467.6750  0.048621  0.816438  91.477861  3.612   
1   5002        HN  PI 656011  512.3625  0.043236  0.768144  76.626487  2.916   
2   5003        HN  PI 576347  606.6625  0.033848  0.751805  89.492182  3.749   

       P     K     Mg     Ca      S     Fe    Mn    B    Cu    Zn      X350  \
0  0.381  1.93  0.245  0.674  0.206  171.0  31.0  6.4  17.6  28.0  0.085242   
1  0.387  2.24  0.143  0.447  0.196  134.0  34.0  4.6  12.5  27.0  0.053529   
2  0.492  1.54  0.260  0.583  0.196  159.0  36.0  5.1  15.4  32.0  0.133649   

       X351      X352      X353      X354      X355      X356      X357  \
0  0.084198  0.073049  0.062852  0.071412  0.076959  0.086402  0.089655   
1  0.087761  0.089831  0.066536  0.070464  0.065440  0.057905  0.061879   
2  0.113164  0.095398  0.095292  0.097985  0.089531  0.085457  0.086694   

       X358      X359      X360      X361      X362      X363      X364  \
0  0.068680  0.077627  0.075629  0.049378  0.047664  0.048732  0.053430   
1  0.087529  0.083688  0.066741  0.054267  0.042131  0.050978  0.056994   
2  0.082119  0.090674  0.082183  0.057630  0.074017  0.063699  0.056483   

       X365      X366      X367      X368      X369      X370      X371  \
0  0.059725  0.043177  0.055788  0.069612  0.049814  0.054452  0.055179   
1  0.045107  0.046368  0.043490  0.042569  0.050927  0.046258  0.041853   
2  0.072555  0.051468  0.052361  0.063759  0.055830  0.039474  0.044329   

       X372      X373      X374      X375      X376      X377      X378  \
0  0.045720  0.038621  0.047542  0.053812  0.049443  0.042255  0.043361   
1  0.043365  0.048262  0.047062  0.048264  0.051650  0.044692  0.043194   
2  0.059886  0.055076  0.055611  0.054215  0.045810  0.032091  0.028689   

       X379      X380      X381      X382      X383      X384      X385  \
0  0.048633  0.051029  0.044424  0.043408  0.041854  0.032599  0.041451   
1  0.040966  0.035022  0.041995  0.044352  0.042166  0.041462  0.043841   
2  0.033169  0.038722  0.042077  0.040161  0.037917  0.041208  0.046213   

       X386      X387      X388      X389      X390      X391      X392  \
0  0.048299  0.048850  0.050056  0.046709  0.043648  0.042465  0.038687   
1  0.043980  0.042063  0.041588  0.038251  0.035009  0.034469  0.037531   
2  0.048145  0.046461  0.043884  0.043052  0.039607  0.035373  0.041091   

       X393      X394      X395      X396      X397      X398      X399  \
0  0.046113  0.051060  0.044858  0.047175  0.049994  0.049110  0.043823   
1  0.040736  0.042420  0.042195  0.041240  0.040235  0.039823  0.040379   
2  0.045182  0.045669  0.043754  0.042794  0.041254  0.040067  0.040752   

       X400      X401      X402      X403      X404      X405      X406  \
0  0.043862  0.041952  0.039572  0.044624  0.044988  0.046128  0.048967   
1  0.041654  0.042781  0.042810  0.041331  0.044993  0.048847  0.048443   
2  0.043151  0.043261  0.042180  0.044544  0.044126  0.043205  0.043584   

       X407      X408      X409      X410      X411      X412      X413  \
0  0.043201  0.043568  0.048380  0.051787  0.049475  0.048316  0.046960   
1  0.042648  0.044995  0.048170  0.044979  0.047369  0.049684  0.049955   
2  0.044392  0.045137  0.045063  0.044390  0.046864  0.045013  0.043726   

       X414      X415      X416      X417      X418      X419      X420  \
0  0.041976  0.046816  0.049948  0.048506  0.050128  0.048849  0.048119   
1  0.048659  0.048421  0.048269  0.048416  0.050394  0.048258  0.048416   
2  0.050980  0.051151  0.049499  0.049354  0.050059  0.049096  0.048275   

       X421      X422      X423      X424      X425      X426      X427  \
0  0.050257  0.051968  0.050424  0.047950  0.047706  0.047331  0.047042   
1  0.052975  0.049087  0.050950  0.054511  0.052481  0.052212  0.052104   
2  0.048961  0.049973  0.049505  0.048687  0.049145  0.049398  0.051126   

       X428      X429      X430      X431      X4

In [110]:
dff.set_index('PlotID', inplace = True)
yld_red_copy = yld_red.copy()
yld_red_copy.set_index('PlotID',inplace = True)
dff.head(3)

Treatment         PI       CHL       EWT       LWC        SLA      N  \
PlotID                                                                        
5001          HN  PI 656057  467.6750  0.048621  0.816438  91.477861  3.612   
5002          HN  PI 656011  512.3625  0.043236  0.768144  76.626487  2.916   
5003          HN  PI 576347  606.6625  0.033848  0.751805  89.492182  3.749   

            P     K     Mg     Ca      S     Fe    Mn    B    Cu    Zn  \
PlotID                                                                   
5001    0.381  1.93  0.245  0.674  0.206  171.0  31.0  6.4  17.6  28.0   
5002    0.387  2.24  0.143  0.447  0.196  134.0  34.0  4.6  12.5  27.0   
5003    0.492  1.54  0.260  0.583  0.196  159.0  36.0  5.1  15.4  32.0   

            X350      X351      X352      X353      X354      X355      X356  \
PlotID                                                                         
5001    0.085242  0.084198  0.073049  0.062852  0.071412  0.076959  0.086402   
5002    0.053529  0.087761  0.089831  0.066536  0.070464  0.065440  0.057905   
5003    0.133649  0.113164  0.095398  0.095292  0.097985  0.089531  0.085457   

            X357      X358      X359      X360      X361      X362      X363  \
PlotID                                                                         
5001    0.089655  0.068680  0.077627  0.075629  0.049378  0.047664  0.048732   
5002    0.061879  0.087529  0.083688  0.066741  0.054267  0.042131  0.050978   
5003    0.086694  0.082119  0.090674  0.082183  0.057630  0.074017  0.063699   

            X364      X365      X366      X367      X368      X369      X370  \
PlotID                                                                         
5001    0.053430  0.059725  0.043177  0.055788  0.069612  0.049814  0.054452   
5002    0.056994  0.045107  0.046368  0.043490  0.042569  0.050927  0.046258   
5003    0.056483  0.072555  0.051468  0.052361  0.063759  0.055830  0.039474   

            X371      X372      X373      X374      X375      X376      X377  \
PlotID                                                                         
5001    0.055179  0.045720  0.038621  0.047542  0.053812  0.049443  0.042255   
5002    0.041853  0.043365  0.048262  0.047062  0.048264  0.051650  0.044692   
5003    0.044329  0.059886  0.055076  0.055611  0.054215  0.045810  0.032091   

            X378      X379      X380      X381      X382      X383      X384  \
PlotID                                                                         
5001    0.043361  0.048633  0.051029  0.044424  0.043408  0.041854  0.032599   
5002    0.043194  0.040966  0.035022  0.041995  0.044352  0.042166  0.041462   
5003    0.028689  0.033169  0.038722  0.042077  0.040161  0.037917  0.041208   

            X385      X386      X387      X388      X389      X390      X391  \
PlotID                                                                         
5001    0.041451  0.048299  0.048850  0.050056  0.046709  0.043648  0.042465   
5002    0.043841  0.043980  0.042063  0.041588  0.038251  0.035009  0.034469   
5003    0.046213  0.048145  0.046461  0.043884  0.043052  0.039607  0.035373   

            X392      X393      X394      X395      X396      X397      X398  \
PlotID                                                                         
5001    0.038687  0.046113  0.051060  0.044858  0.047175  0.049994  0.049110   
5002    0.037531  0.040736  0.042420  0.042195  0.041240  0.040235  0.039823   
5003    0.041091  0.045182  0.045669  0.043754  0.042794  0.041254  0.040067   

            X399      X400      X401      X402      X403      X404      X405  \
PlotID                                                                         
5001    0.043823  0.043862  0.041952  0.039572  0.044624  0.044988  0.046128   
5002    0.040379  0.041654  0.042781  0.042810  0.041331  0.044993  0.048847   
5003    0.040752  0.043151  0.043261  0.042180  0.044544  0.044126  0.043205   

            X406      X407      

In [111]:
list(yld_red.columns)

['PlotID', 'PI', 'Treatment', 'yield', 'DaysToBloom', 'PlantHeight']

In [112]:
dff[['PI', 'Treatment', 'yield', 'DaysToBloom', 'PlantHeight']].isnull().sum()

PI               0
Treatment        0
yield          202
DaysToBloom    202
PlantHeight    202
dtype: int64

In [113]:
yld_red_copy.head(3)

PI Treatment  yield  DaysToBloom  PlantHeight
PlotID                                                      
8390    PI 655998        HN   20.0         62.0         86.0
8364    PI 576396        HN   38.0         64.0         90.0
8351    PI 656023        HN   22.4         73.0        150.0

In [114]:
#imputation
dff = dff.combine_first(yld_red_copy)

In [115]:
dff[['PI', 'Treatment', 'yield', 'DaysToBloom', 'PlantHeight']].isnull().sum()

PI               0
Treatment        0
yield          103
DaysToBloom    103
PlantHeight    103
dtype: int64

In [117]:
dff.reset_index(inplace = True)
dff.to_csv('../data/data_red_imputed-1.2.csv')

In [118]:
dff.head()

PlotID    B       CHL     Ca    Cu  DaysToBloom       EWT     Fe     K  \
0    5001  6.4  467.6750  0.674  17.6         83.0  0.048621  171.0  1.93   
1    5002  4.6  512.3625  0.447  12.5         76.0  0.043236  134.0  2.24   
2    5003  5.1  606.6625  0.583  15.4          NaN  0.033848  159.0  1.54   
3    5004  NaN       NaN    NaN   NaN         71.0       NaN    NaN   NaN   
4    5005  NaN       NaN    NaN   NaN         71.0       NaN    NaN   NaN   

        LWC     Mg    Mn      N      P         PI  PlantHeight      S  \
0  0.816438  0.245  31.0  3.612  0.381  PI 656057        128.0  0.206   
1  0.768144  0.143  34.0  2.916  0.387  PI 656011        110.0  0.196   
2  0.751805  0.260  36.0  3.749  0.492  PI 576347          NaN  0.196   
3       NaN    NaN   NaN    NaN    NaN  PI 533807         82.0    NaN   
4       NaN    NaN   NaN    NaN    NaN  PI 533901         88.0    NaN   

         SLA Treatment     X1000     X1001     X1002     X1003     X1004  \
0  91.477861        HN  0.474277  0.474403  0.474529  0.474655  0.474781   
1  76.626487        HN  0.491301  0.491336  0.491371  0.491406  0.491441   
2  89.492182        HN  0.516873  0.517113  0.517353  0.517592  0.517832   
3        NaN        HN       NaN       NaN       NaN       NaN       NaN   
4        NaN        HN       NaN       NaN       NaN       NaN       NaN   

      X1005     X1006     X1007     X1008     X1009     X1010     X1011  \
0  0.474907  0.475033  0.475158  0.475284  0.475410  0.475536  0.475688   
1  0.491476  0.491511  0.491546  0.491581  0.491616  0.491651  0.491807   
2  0.518071  0.518311  0.518551  0.518790  0.519030  0.519270  0.519422   
3       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
4       NaN       NaN       NaN       NaN       NaN       NaN       NaN   

      X1012     X1013     X1014     X1015     X1016     X1017     X1018  \
0  0.475883  0.476092  0.476295  0.476547  0.476731  0.476871  0.477020   
1  0.491928  0.492030  0.492137  0.492215  0.492333  0.492478  0.492602   
2  0.519596  0.519787  0.519946  0.520070  0.520249  0.520458  0.520623   
3       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
4       NaN       NaN       NaN       NaN       NaN       NaN       NaN   

      X1019     X1020     X1021     X1022     X1023     X1024     X1025  \
0  0.477147  0.477276  0.477380  0.477523  0.477682  0.477841  0.478011   
1  0.492748  0.492863  0.492936  0.493039  0.493149  0.493257  0.493370   
2  0.520799  0.520966  0.521104  0.521231  0.521360  0.521487  0.521602   
3       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
4       NaN       NaN       NaN       NaN       NaN       NaN       NaN   

      X1026     X1027     X1028     X1029     X1030     X1031     X1032  \
0  0.478220  0.478387  0.478526  0.478696  0.478880  0.479037  0.479199   
1  0.493498  0.493618  0.493741  0.493842  0.493932  0.494028  0.494113   
2  0.521681  0.521786  0.521905  0.522024  0.522147  0.522257  0.522367   
3       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
4       NaN       NaN       NaN       NaN       NaN       NaN       NaN   

      X1033     X1034     X1035     X1036     X1037     X1038     X1039  \
0  0.479345  0.479467  0.479586  0.479698  0.479813  0.479914  0.480025   
1  0.494193  0.494277  0.494364  0.494443  0.494519  0.494613  0.494685   
2  0.522483  0.522612  0.522701  0.522747  0.522845  0.522958  0.523044   
3       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
4       NaN       NaN       NaN       NaN       NaN       NaN       NaN   

      X1040     X1041     X1042     X1043     X1044     X1045     X1046  \
0  0.480153  0.480272  0.480370  0.480458  0.480537  0.480597  0.480662   
1  0.494733  0.494779  0.494834  0.494890  0.494936  0.494995  0.495023   
2  0.523150  0.523272  0.523350  0.523371  0.523421  0.523492  0.523525   
3       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
4       NaN   